# 0 前提作業

## 0_0 ライブラリのインポート/ファイルの読み込み

In [4]:
#ライブラリのインポート
import glob
import pandas as pd
import pandas_profiling as pdp
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import lightgbm as lgb
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error as mae

In [5]:
#ファイルの読み込み
files = glob.glob("../data/train/*.csv")
data_list = []
for file in files:
    data_list.append(pd.read_csv(file, index_col=0))
data_list
df = pd.concat(data_list)
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 692882 entries, 1088170 to 47027230
Data columns (total 27 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   種類            692882 non-null  object 
 1   地域            0 non-null       float64
 2   市区町村コード       692882 non-null  int64  
 3   都道府県名         692882 non-null  object 
 4   市区町村名         692882 non-null  object 
 5   地区名           692221 non-null  object 
 6   最寄駅：名称        690187 non-null  object 
 7   最寄駅：距離（分）     669761 non-null  object 
 8   間取り           668450 non-null  object 
 9   面積（㎡）         692882 non-null  object 
 10  土地の形状         0 non-null       float64
 11  間口            0 non-null       float64
 12  延床面積（㎡）       0 non-null       float64
 13  建築年           672808 non-null  object 
 14  建物の構造         675496 non-null  object 
 15  用途            630269 non-null  object 
 16  今後の利用目的       328144 non-null  object 
 17  前面道路：方位       0 non-null       float64
 

 ## 0_1 元データ列一覧（削除したものは赤字）  
---  ------        --------------   -----  
 0   種類           692882 non-null  object <br>
 &emsp;<font color="red">1値のみの格納のため削除（1値：中古マンション等）</font> <br>
 1   地域            0 non-null       float64 <br>
 &emsp;<font color="red">all-nullのため削除</font> <br>
 2   市区町村コード       692882 non-null  int64  <br>
 3   都道府県名         692882 non-null  object <br>
 4   市区町村名         692882 non-null  object <br>
 &emsp;<font color="red">市区町村名と同じ情報のため削除</font> <br>
 5   地区名           692221 non-null  object <br>
 6   最寄駅：名称        690187 non-null  object <br>
 7   最寄駅：距離（分）     669761 non-null  object <br>
 8   間取り           668450 non-null  object <br>
 9   面積（㎡）         692882 non-null  object <br>
 10  土地の形状         0 non-null       float64 <br>
 &emsp;<font color="red">all-nullのため削除</font> <br>
 11  間口            0 non-null       float64 <br>
 &emsp;<font color="red">all-nullのため削除</font> <br>
 12  延床面積（㎡）       0 non-null       float64 <br>
 &emsp;<font color="red">all-nullのため削除</font> <br>
 13  建築年           672808 non-null  object <br>
 14  建物の構造         675496 non-null  object <br>
 15  用途            630269 non-null  object <br>
 16  今後の利用目的       328144 non-null  object <br>
 17  前面道路：方位       0 non-null       float64 <br>
 &emsp;<font color="red">all-nullのため削除</font> <br>
 18  前面道路：種類       0 non-null       float64 <br>
 &emsp;<font color="red">all-nullのため削除</font> <br>
 19  前面道路：幅員（ｍ）    0 non-null       float64 <br>
 &emsp;<font color="red">all-nullのため削除</font> <br>
 20  都市計画          673457 non-null  object <br>
 21  建ぺい率（％）       669257 non-null  float64 <br>
 22  容積率（％）        669257 non-null  float64 <br>
 23  取引時点          692882 non-null  object <br>
 24  改装            628856 non-null  object <br>
 25  取引の事情等        18679 non-null   object <br>
 26  取引価格（総額）_log  692882 non-null  float64 <br>

In [21]:
#不要列の削除
df = df.drop(columns="種類", axis=1)
df = df.drop(columns="地域", axis=1)
df = df.drop(columns="市区町村名", axis=1)
df = df.drop(columns="土地の形状", axis=1)
df = df.drop(columns="間口", axis=1)
df = df.drop(columns="延床面積（㎡）", axis=1)
df = df.drop(columns="前面道路：方位", axis=1)
df = df.drop(columns="前面道路：種類", axis=1)
df = df.drop(columns="前面道路：幅員（ｍ）", axis=1)
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 692882 entries, 1088170 to 47027230
Data columns (total 18 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   市区町村コード       692882 non-null  int64  
 1   都道府県名         692882 non-null  object 
 2   地区名           692221 non-null  object 
 3   最寄駅：名称        690187 non-null  object 
 4   最寄駅：距離（分）     669761 non-null  object 
 5   間取り           668450 non-null  object 
 6   面積（㎡）         692882 non-null  object 
 7   建築年           672808 non-null  object 
 8   建物の構造         675496 non-null  object 
 9   用途            630269 non-null  object 
 10  今後の利用目的       328144 non-null  object 
 11  都市計画          673457 non-null  object 
 12  建ぺい率（％）       669257 non-null  float64
 13  容積率（％）        669257 non-null  float64
 14  取引時点          692882 non-null  object 
 15  改装            628856 non-null  object 
 16  取引の事情等        18679 non-null   object 
 17  取引価格（総額）_log  692882 non-null  float64
d

# 1 EDA

In [22]:
#EDA概略
pdp.ProfileReport(df)

Summarize dataset:   0%|          | 0/33 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## 1_1 EDA_都道府県

In [23]:
#北側から順にint型でナンバリングに置換する。

In [24]:
#置換用のリスト型
pref_jiscode = {
    "北海道": 1, "青森県": 2, "岩手県": 3, "宮城県": 4, "秋田県": 5, "山形県": 6, "福島県": 7, "茨城県": 8, "栃木県": 9, "群馬県": 10, "埼玉県": 11, "千葉県": 12,
    "東京都": 13, "神奈川県": 14, "新潟県": 15, "富山県": 16, "石川県": 17, "福井県": 18, "山梨県": 19, "長野県": 20, "岐阜県": 21, "静岡県": 22, "愛知県": 23, "三重県": 24,
    "滋賀県": 25, "京都府": 26, "大阪府": 27, "兵庫県": 28, "奈良県": 29, "和歌山県": 30, "鳥取県": 31, "島根県": 32, "岡山県": 33, "広島県": 34, "山口県": 35, "徳島県": 36,
    "香川県": 37, "愛媛県": 38, "高知県": 39, "福岡県": 40, "佐賀県": 41, "長崎県": 42, "熊本県": 43, "大分県": 44, "宮崎県": 45, "鹿児島県": 46, "沖縄県": 47
}

In [25]:
#型の変換
df["都道府県名_num"] = df["都道府県名"].replace(pref_jiscode).astype(int)
df = df.drop(columns="都道府県名", axis=1)

## 1_2 EDA_最寄駅：距離（分）

In [26]:
replace_min = {
    "30分?60分":45,
    "1H?1H30":75,
    "2H?":120,
    "1H30?2H":105
}
df["最寄駅：距離（分）_min"] = df["最寄駅：距離（分）"].replace(replace_min).astype(float)
df = df.drop(columns="最寄駅：距離（分）", axis=1)

## 1_3 EDA_間取り

In [27]:
#変更なしとする
pd.set_option('display.max_rows', None)
df["間取り"].value_counts()

３ＬＤＫ       294627
１Ｋ         101649
２ＬＤＫ       100143
４ＬＤＫ        62869
１ＬＤＫ        29665
２ＤＫ         21946
１ＤＫ         20078
３ＤＫ         12540
１Ｒ           7227
オープンフロア      5464
２ＬＤＫ＋Ｓ       4044
４ＤＫ          1780
２Ｋ           1347
１ＬＤＫ＋Ｓ       1178
３ＬＤＫ＋Ｓ        957
５ＬＤＫ          889
３Ｋ            496
２ＤＫ＋Ｓ         464
４ＬＤＫ＋Ｓ        167
４Ｋ            161
３ＬＫ           113
５ＤＫ            98
スタジオ           85
１ＤＫ＋Ｓ          79
３ＤＫ＋Ｓ          76
６ＬＤＫ           37
５ＬＤＫ＋Ｓ         35
メゾネット          33
４ＤＫ＋Ｓ          22
１Ｋ＋Ｓ           21
２ＬＫ            21
１Ｒ＋Ｓ           18
１ＬＫ            13
２Ｋ＋Ｓ           11
３ＬＤ            10
１Ｌ              9
２ＬＤ＋Ｓ           9
４Ｌ＋Ｋ            8
３ＬＤＫ＋Ｋ          7
６ＤＫ             5
３ＬＤ＋Ｓ           5
７ＬＤＫ            5
５Ｋ              4
２ＬＫ＋Ｓ           4
１ＬＤ＋Ｓ           3
４ＬＤＫ＋Ｋ          3
３Ｋ＋Ｓ            3
６ＬＤＫ＋Ｓ          3
８ＬＤＫ            2
２Ｌ              2
３Ｄ              2
７ＬＤＫ＋Ｓ          2
８ＬＤＫ＋Ｓ          1
１ＤＫ＋Ｋ           1
１Ｌ＋Ｓ            1
５ＬＤＫ＋Ｋ    

## 1_4 EDA_面積（㎡）

In [28]:
#全てint型に変更（"2000m2以上"を2000に変更、）
df["面積（㎡）_num"] = df["面積（㎡）"].replace("2000㎡以上", 2000).astype(int)
df = df.drop(columns="面積（㎡）", axis=1)

## 1_5 EDA_建築年

In [57]:
#起点を2022年とする（建築0年は存在しないこととする）。 
#year_listに建築年：経過年数のリストを作成する。
year_list = {}
for i in df["建築年"].value_counts().keys():
    if ("令和" in i):
        year_list[i] = 4 - int(i[2:3])
    elif ("平成" in i):
        try:
            year_list[i] = 34 - int(i[2:4])
        except ValueError:
            year_list[i] = 34 - int(i[2:3])
    elif ("昭和" in i):
        year_list[i] = 97 - int(i[2:4])
    elif ("戦前" in i):
        year_list[i] = 77
    else:print(i)    #未処理確認

#year_listを元に経過年数の列"建築年_year"を作成。
df["建築年_year"] = df["建築年"].replace(year_list)

#元列の"建築年"列を削除
df = df.drop(columns="建築年", axis=1)

## 1_6 EDA_建物の構造

In [60]:
df["建物の構造"].value_counts()

ＲＣ            468545
ＳＲＣ           201020
鉄骨造             4567
ＳＲＣ、ＲＣ           741
ＲＣ、鉄骨造           341
ＳＲＣ、鉄骨造          151
木造                85
ブロック造             22
軽量鉄骨造             20
ＳＲＣ、ＲＣ、鉄骨造         2
ＲＣ、ブロック造           1
ＲＣ、木造              1
Name: 建物の構造, dtype: int64

In [64]:
#各構造毎に得点を付与（強度が強いものほど高強度、複数組み合わせの場合は平均をとる）
str_stength={
    "ＳＲＣ":6,
    "ＳＲＣ、ＲＣ":5.5,
    "ＲＣ":5,
    "ＳＲＣ、ＲＣ、鉄骨造":5,
    "ＳＲＣ、鉄骨造":5,
    "ＲＣ、鉄骨造":4.5,
    "鉄骨造":4,
    "ＲＣ、ブロック造":3.5,
    "軽量鉄骨造":3,
    "ＲＣ、木造":3,
    "ブロック造":2,
    "木造":1
}
#str_stengthを元に"建物の構造_num"を作成。
df["建物の構造_num"] = df["建物の構造"].replace(str_stength)

#元列の"建物の構造"列を削除
df = df.drop(columns="建物の構造", axis=1)

## 1_7 EDA_用途

In [68]:
#変更なしとする
df["用途"].value_counts()

住宅               622443
事務所                3666
店舗                 2970
その他                 818
駐車場                 104
事務所、店舗               66
倉庫                   59
住宅、店舗                56
住宅、事務所               35
住宅、その他               18
住宅、駐車場                7
工場                    7
倉庫、店舗                 4
作業場                   3
倉庫、駐車場                3
駐車場、店舗                2
店舗、その他                2
事務所、倉庫                2
住宅、店舗、その他             1
住宅、事務所、駐車場、店舗         1
事務所、駐車場               1
住宅、倉庫                 1
Name: 用途, dtype: int64

## 1_8 EDA_今後の利用目的

In [69]:
#変更無しとする。
df["今後の利用目的"].value_counts()

住宅     304734
その他     18564
事務所      3621
店舗       1225
Name: 今後の利用目的, dtype: int64

## 1_9 EDA_都市計画

In [71]:
#変更無しとする。
df["都市計画"].value_counts()

商業地域                      188963
第１種中高層住居専用地域              107756
第１種住居地域                   105832
準工業地域                      79171
近隣商業地域                     69843
第２種住居地域                    31889
第２種中高層住居専用地域               31789
第１種低層住居専用地域                21036
工業地域                       17344
準住居地域                      13732
市街化調整区域                     4348
第２種低層住居専用地域                  948
市街化区域及び市街化調整区域外の都市計画区域       322
工業専用地域                       240
都市計画区域外                      237
準都市計画区域                        7
Name: 都市計画, dtype: int64

## 1_10 EDA_建ぺい率（％）

In [72]:
#変更無しとする。
df["建ぺい率（％）"].value_counts()

60.0    378933
80.0    269123
50.0     15276
40.0      4990
30.0       502
70.0       433
Name: 建ぺい率（％）, dtype: int64

## 1_11 EDA_容積率（％）

In [74]:
#変更無しとする。
df["容積率（％）"].value_counts()

200.0     317885
400.0     113408
300.0      92860
500.0      44597
600.0      42009
150.0      24436
100.0      10460
700.0       9017
800.0       7430
80.0        6319
1000.0       382
60.0         324
900.0         79
50.0          29
1200.0        11
1100.0         6
1300.0         5
Name: 容積率（％）, dtype: int64

## 1_12 EDA_取引時点

In [89]:
#trade_timingに取引時点：取引時点の年のint型のリストを作成する。
trade_timing = {}
for i in df["取引時点"].value_counts().keys():
    if("1四半期" in i):
        num = float(i[0:4]+".25")
        trade_timing[i] = num
    elif("2四半期" in i):
        num = float(i[0:4]+".50")
        trade_timing[i] = num
    elif("3四半期" in i):
        num = float(i[0:4]+".75")
        trade_timing[i] = num
    elif("4四半期" in i):
        num = float(i[0:4]+".99")
        trade_timing[i] = num
    else:print("test")    #未処理確認
#trade_timingを元に取引時点の列"取引時点_num"を作成。
df["取引時点_num"] = df["取引時点"].replace(trade_timing)

#元列の"取引時点"列を削除
df = df.drop(columns="取引時点", axis=1)

In [90]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 692882 entries, 1088170 to 47027230
Data columns (total 18 columns):
 #   Column         Non-Null Count   Dtype  
---  ------         --------------   -----  
 0   市区町村コード        692882 non-null  int64  
 1   地区名            692221 non-null  object 
 2   最寄駅：名称         690187 non-null  object 
 3   間取り            668450 non-null  object 
 4   用途             630269 non-null  object 
 5   今後の利用目的        328144 non-null  object 
 6   都市計画           673457 non-null  object 
 7   建ぺい率（％）        669257 non-null  float64
 8   容積率（％）         669257 non-null  float64
 9   改装             628856 non-null  object 
 10  取引の事情等         18679 non-null   object 
 11  取引価格（総額）_log   692882 non-null  float64
 12  都道府県名_num      692882 non-null  int32  
 13  最寄駅：距離（分）_min  669761 non-null  float64
 14  面積（㎡）_num      692882 non-null  int32  
 15  建築年_year       672808 non-null  float64
 16  建物の構造_num      675496 non-null  float64
 17  取引時点_num       692882

## 1_13 EDA_改装

In [91]:
#変更無しとする。
df["改装"].value_counts()

未改装    452925
改装済    175931
Name: 改装, dtype: int64

## 1_14 EDA_取引の事情等

In [92]:
#変更無しとする。
df["取引の事情等"].value_counts()

調停・競売等              17541
関係者間取引                902
その他事情有り               106
瑕疵有りの可能性               76
他の権利・負担付き              46
他の権利・負担付き、調停・競売等        3
関係者間取引、調停・競売等           2
調停・競売等、瑕疵有りの可能性         2
関係者間取引、瑕疵有りの可能性         1
Name: 取引の事情等, dtype: int64

## 1_15 EDA_まとめ

In [100]:
df.shape

(692882, 18)

In [102]:
#列順の修正
index_array = ["市区町村コード", "都道府県名_num", "地区名", "最寄駅：名称", "最寄駅：距離（分）_min",
               "間取り", "面積（㎡）_num", "建築年_year", "建物の構造_num", "用途",
              "今後の利用目的", "都市計画", "建ぺい率（％）", "容積率（％）", "取引時点_num",
              "改装", "取引の事情等", "取引価格（総額）_log"]
df = df.reindex(columns=index_array)
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 692882 entries, 1088170 to 47027230
Data columns (total 18 columns):
 #   Column         Non-Null Count   Dtype  
---  ------         --------------   -----  
 0   市区町村コード        692882 non-null  int64  
 1   都道府県名_num      692882 non-null  int32  
 2   地区名            692221 non-null  object 
 3   最寄駅：名称         690187 non-null  object 
 4   最寄駅：距離（分）_min  669761 non-null  float64
 5   間取り            668450 non-null  object 
 6   面積（㎡）_num      692882 non-null  int32  
 7   建築年_year       672808 non-null  float64
 8   建物の構造_num      675496 non-null  float64
 9   用途             630269 non-null  object 
 10  今後の利用目的        328144 non-null  object 
 11  都市計画           673457 non-null  object 
 12  建ぺい率（％）        669257 non-null  float64
 13  容積率（％）         669257 non-null  float64
 14  取引時点_num       692882 non-null  float64
 15  改装             628856 non-null  object 
 16  取引の事情等         18679 non-null   object 
 17  取引価格（総額）_log   692882

In [106]:
for col in ["地区名", "最寄駅：名称", "間取り", "用途", "今後の利用目的", "都市計画", "改装", "取引の事情等"]:
    df[col] = df[col].astype("category")

In [107]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 692882 entries, 1088170 to 47027230
Data columns (total 18 columns):
 #   Column         Non-Null Count   Dtype   
---  ------         --------------   -----   
 0   市区町村コード        692882 non-null  int64   
 1   都道府県名_num      692882 non-null  int32   
 2   地区名            692221 non-null  category
 3   最寄駅：名称         690187 non-null  category
 4   最寄駅：距離（分）_min  669761 non-null  float64 
 5   間取り            668450 non-null  category
 6   面積（㎡）_num      692882 non-null  int32   
 7   建築年_year       672808 non-null  float64 
 8   建物の構造_num      675496 non-null  float64 
 9   用途             630269 non-null  category
 10  今後の利用目的        328144 non-null  category
 11  都市計画           673457 non-null  category
 12  建ぺい率（％）        669257 non-null  float64 
 13  容積率（％）         669257 non-null  float64 
 14  取引時点_num       692882 non-null  float64 
 15  改装             628856 non-null  category
 16  取引の事情等         18679 non-null   category
 17  取引